In [143]:
from dotenv import load_dotenv
import os
load_dotenv(override=True)
chroma_client=os.environ["CHROMA_DB_CLIEN"]
chroma_token=os.environ["CHROMA_TOKEN"]

In [2]:
import chromadb
from chromadb.config import Settings
client = chromadb.HttpClient(host=chroma_client, port=8000,    settings=Settings(
        chroma_client_auth_provider="chromadb.auth.token_authn.TokenAuthClientProvider",
        chroma_client_auth_credentials=chroma_token
    ))


In [3]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')

In [4]:
collection = client.create_collection("all-my-projects")


In [36]:
document_path=".\documents"

for i in range(1,13):
    with open(f"{document_path}\{i}.text","r") as f:
        document=[f.read()]
        vectors=model.encode(document).astype(float).tolist()
        id  = f"id_{i}"
        ids=[id]
        metadatas=[{"type":"project by djallel"}]
        collection.add(
        ids=ids,
        documents=document,
        embeddings=vectors,
        metadatas=metadatas,
    )
print("done with :", i)

    


done with : 12


In [121]:
def make_context(similars):
    if len(similars)==0:
        return ""
    message = "To provide some context, here are some projects done by djallel that might be related to the question that you need to answer.\n\n"
    for similar in similars:
        message += f"Potentially related projects:\n{similar}\n\n"
    return message

In [43]:
def vector(question):
    return model.encode([question])

In [109]:
def find_similars(question):
    results = collection.query(query_embeddings=vector(question).astype(float).tolist(), n_results=5,include=['documents',"distances"])
    documents = results['documents'][0][:]
    distances=results['distances'][0][:]
    filtered_documents = [
    doc for doc, dist in zip(documents, distances) if dist < 1.7
]
    return filtered_documents

In [115]:
len(find_similars("Dance dinner launch hello"))==0

True

In [ ]:
matches=[]

In [73]:
from openai import OpenAI
openai = OpenAI()

In [80]:
from pypdf import PdfReader
import gradio as gr
reader = PdfReader("documents/CV/CV.pdf")
cv = ""
for page in reader.pages:
    text = page.extract_text()
    if text:
        cv += text



name = "Djallel BRAHMIA"

In [84]:
system_prompt = f"You are acting as {name}. You are answering questions on {name}'s website, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully as possible. \
You are given a summary of {name}'s background and LinkedIn profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
 "
system_prompt += f"\n\## CV:\n{cv}\n\n"

system_prompt += f"With this context, please chat with the user, always staying in character as {name}."


In [131]:

record_unknown_question_json = {
    "name": "record_unknown_question",
    "description": "Always use this tool to record any question that couldn't be answered as you didn't know the answer",
    "parameters": {
        "type": "object",
        "properties": {
            "question": {
                "type": "string",
                "description": "The question that couldn't be answered"
            },
        },
        "required": ["question"],
        "additionalProperties": False
    }
}

In [144]:
import requests

def push(text):
    requests.post(
        "https://api.pushover.net/1/messages.json",
        data={
            "token": os.getenv("PUSHOVER_TOKEN"),
            "user": os.getenv("PUSHOVER_USER"),
            "message": text,
        }
    )

In [145]:
push("test")

In [146]:
def record_unknown_question(question):
    push(f"Recording {question}")
    return {"recorded": "ok"}

In [148]:

tools = [{"type": "function", "function": record_unknown_question_json}]

In [150]:
def handle_tool_call(tool_calls):
        results = []
        for tool_call in tool_calls:
            tool_name = tool_call.function.name
            arguments = json.loads(tool_call.function.arguments)
            print(f"Tool called: {tool_name}", flush=True)
            tool = globals().get(tool_name)
            result = tool(**arguments) if tool else {}
            results.append({"role": "tool","content": json.dumps(result),"tool_call_id": tool_call.id})
        return results

In [128]:
def chat(message,history):
    similars=find_similars(message)

    message+=make_context(similars)
    print(message)
    messages = [{"role": "system", "content": system_prompt}]+history  + [{"role": "user", "content": message}]

    
        # This is the call to the LLM - see that we pass in the tools json

    response = openai.chat.completions.create(model="gpt-4o-mini", messages=messages)

        
        # If the LLM wants to call a tool, we do that!
         
    return response.choices[0].message.content

In [129]:
chat("did you worked on any vr projects? ",[])

did you worked on any vr projects? To provide some context, here are some projects done by djallel that might be related to the question that you need to answer.

Potentially related projects:
🕶️ VR Hanoi Tower Game – Built with WebXR & React
🎮 Project Overview
VR Hanoi Tower is a fully interactive virtual reality adaptation of the classic Tower of Hanoi puzzle game. Developed using WebXR and React, this immersive experience allows users to play directly in their web browser using VR devices like Oculus Quest or supported desktop headsets.

Designed for both fun and educational use, the game challenges players to move a stack of discs between rods following the traditional rules of Hanoi, now reimagined in a 3D virtual space.

🧠 Key Features
🕹️ Interactive 3D Environment
Play the Hanoi Tower puzzle in an immersive VR space using motion controls or click-based interactions.

🌐 WebXR Integration
Seamlessly supports VR headsets through WebXR APIs – no installations required.

⚛️ React + C

'Yes, I have worked on a virtual reality project titled **VR Hanoi Tower Game**, which is a fully interactive adaptation of the classic Tower of Hanoi puzzle game. This project leverages WebXR and React, allowing users to immerse themselves in a 3D environment where they can interact with the game using VR devices such as Oculus Quest or supported desktop headsets.\n\n### Project Overview:\nThe **VR Hanoi Tower Game** is designed to offer both fun and educational opportunities, challenging players to strategically move discs between rods according to the traditional game rules, reimagined within a virtual space.\n\n### Key Features:\n- **Interactive 3D Environment**: The game presents a fully interactive experience where users can utilize motion controls or click-based interactions.\n- **WebXR Integration**: By using the WebXR API, players can engage in the game directly within their web browsers without requiring any installations.\n- **Dynamic Game Logic**: The application implements

In [130]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7866

To create a public link, set `share=True` in `launch()`.


Did you done anything interesting in IA and machine learning?To provide some context, here are some projects done by djallel that might be related to the question that you need to answer.

Potentially related projects:
🧠 ML Toolkit – A Customizable Machine Learning Library in Python
📌 Project Overview
ML Toolkit is a Python-based, modular machine learning library built from scratch to provide a flexible and transparent learning and experimentation environment. It supports a wide range of supervised learning algorithms, including both regression and classification models. Designed with extensibility and clarity in mind, it enables users to understand core ML concepts through hands-on model development and testing.

This toolkit is ideal for those looking to deepen their understanding of machine learning by working directly with algorithmic implementations—without relying on high-level libraries like scikit-learn or TensorFlow.

🧩 Implemented Models
🔍 Classification Algorithms:
Support V